# Quantum Circuit Design through Monte Carlo Tree Search
In this tutorial we are going to show the whole pipeline of the Monte Carlo Tree Search (MCTS) implemented for quantum circuit design.

## Brief intro to the task of quantum circuit design
The goal is finding a quantum circuit that solve a certain problem.  
Let's start from the beginning. What is a quantum circuit? 
A quantum circuit is a model for quantum computation, similar to classical circuits, in which a computation is done on qubits (orizontal line), namely the quantum analogue of bits, through a sequence of quantum gates (boxes).
An example of quantum circuit (random) is below.

In [8]:
# Import library that allow to work with quantum circuits
from qiskit import QuantumCircuit

# Initialize a quantum circuit with 4 qubits
qc = QuantumCircuit(4)
# Add a non-parameterized gate on the 0th qubit 
qc.h(0)
# Add a parameterized gate on each of the four qubits (all with a parameter fixed to 0.5)
for i in range(4):
    qc.ry(0.5, i)
print("You have built your first quantum circuit:")
qc.draw()

# If you want to print the circuit in a fancier way uncomment replace the previous line of code with the following one
# qc.draw("mpl")

You have built your first quantum circuit:


┌───┐   ┌─────────┐
q_0: ───┤ H ├───┤ Ry(0.5) ├
     ┌──┴───┴──┐└─────────┘
q_1: ┤ Ry(0.5) ├───────────
     ├─────────┤           
q_2: ┤ Ry(0.5) ├───────────
     ├─────────┤           
q_3: ┤ Ry(0.5) ├───────────
     └─────────┘

Why are we interested in those circuits?
It is possible to encode some problems, either classical or quantum, into the framework of quantum circuits. In this context, solving the problem means finding a suitable quantum circuit that represet in such a way the solution.

How do people find the right structure of the circuit for a given problem?
In certain domains, it is possible to exploit the structure of the original problem to guess a suitable quantum circuits. In other domains, we ha no clue and we either try (cry) with extremely computational expensive exhaustive search or with other "smarter" search techniques.

What do you mean with "quantum circuit design"?
Designing a quantum circuit means finding the ordered sequence of gates (parameterized and not-parameterized) applied to the qubits that give raise to the circuit that can solve a given problem.
You can imagine the task of designing a quantum circuit as the quantum analogue of the design of Neural Networks. In neural networks you have to find the stucture (number of neurons, hidden layers, activation function, etc.) that allows to solve the problem after the learning of the parameters (weights). Similarly, in the quantum setting, we also have to find the structure (sequence of gates), that allows to solve the problem after the learning of the parameters (angle parameters of the parameterized gates).
However, the search space defined by quantum circuits is extremely big (exponential in the number of qubits) and we want to find automatic and efficient way to get "good" circuits. Namely, we want a "shallow circuit" that evaluated on an objevtive function gives a value "close" to the optimum.

Why do you want a shallow circuit?
Currently available quantum computers suffer of several limitation The most importantS relate to the number of qubits we dispose and the number of gates we can apply 

Nice! But we have been told that we do NOT need quantum for this project. So what?
In this project, we will provide you some problems encoded in the circuit-based quantum computing setting in a black-box form. That means, that the problems are provided as real-valued function on the domain of quantum circuits. This functions will be your objective functions and your goal is to minimize them.
You don't have to understand what exactly those "quantum" functions do, but you only need to work with MCTS and its variants to get hopefully better results (lower values of the objective functions).

## Objective functions


Here we define an objective function to optimize. The objective function is a real-valued function defined on quantum circuits. You can find examples in the file evaluation_functions.py about quantum chemistry, systems of linear equations and combinatorial optimization (Max-Cut).  

Let's take a famous example from the domain of quantum chemistry. The study of molecules involves quantum phenomena and as such this fiels is considered one of the most promising application for quantum computing.
Here we will estimate the ground state energy of the hydrogen molecule $H_2$ by using an hybrid classical-quantum algorithm, the variational quantum eigensolver. 

In the following we evaluate the quantum circuit created above as a solution for the ground state energy problem on $H_2$.

You can change the problem as described below. The number of qubits required for each problem is in the dictionary named "N_QUBITS" in file main.py

In [9]:

import evaluation_functions as evf

# The quantum problems provided as black-box are in evf
problem = evf.h2    # one of the problem provided
# You can equivalently work with the other evaluation functions (pay attention to the number of qubits required, as it depends on the evaluation function):
"""
# Quantum Chemistry But on different molecules
problem = evf.lih
problem = evf.h2o
# Different systems of linear equations
problem = evf.vqls_0
problem = evf.vqls_1
# NP-Hard problem: MAX-CUT
problem = evf.max_cut

"""
cost_value = problem(qc, cost=True)

print(f"Given the quantum circuit below: \n{qc}\n the objective function returns: {cost_value}")

Given the quantum circuit below: 
        ┌───┐   ┌─────────┐
q_0: ───┤ H ├───┤ Ry(0.5) ├
     ┌──┴───┴──┐└─────────┘
q_1: ┤ Ry(0.5) ├───────────
     ├─────────┤           
q_2: ┤ Ry(0.5) ├───────────
     ├─────────┤           
q_3: ┤ Ry(0.5) ├───────────
     └─────────┘           
 the objective function returns: -0.2318460796537938


## Link Quantum to Classical
Once we have defined the problem, we can use MCTS in order to design a first guess, also known as "ansatz", for the initial quantum circuit that.
We hope you did not get scared with this brief intro into the "quantum world". Anyways, from now on you will only work with classical techniques. Here there is the link we created between the classical and quantum "world":
- Node: Quantum Circuit
- Moves: apply changes to the circuit. There are 4 possible changes implemented:
    1. Add new random gate in random position
    2. Remove radom gate in random position
    3. Swap a random gate with a new gate in the same position
    4. Change the angle parameter in a parameterized gate
- Objective function: quantum black box provided


    


## Your MCTS baseline
Below you will see how does your baseline work

In [10]:
# Number of qubits required by the problem. In the problem of estimating the ground state energy of the ydrogen we only need 4 qubits (For all the other problems we provide you of all the information)
variable_qubits = 4
ancilla_qubits = 0
# Max depth of the circuit that we want to search with the MCTS
max_depth = 10
# Computational budget we provide MCTS to explore the search space. it is equivalent to the number of new nodes evaluated
budget = 1000
# Set to false MCTS use an adaptive technique to fix the branching factor of each node. This allows to explore more the most promising nodes. Set to an integer, the branching factor will be fixed for all nodes of the tree.
branches = False

criteria = "average_value"
rollout_type = 'classic'
roll_out_steps = 2
choices = {'a': 50, 'd': 10, 's': 20, 'c': 20, 'p': 0}
epsilon = None
stop_deterministic = False
# Hyperparametrs of MCTS
ucb = 0.4
pw_C = 1
pw_alpha = 0.3


Below we define the root node by inizializing an empty circuit. The search starts from that node and MCTS will search for the best.

In [11]:
import mcts
from structure import Circuit
# Initialize the search by creating an empty circuit in the root node
root = mcts.Node(Circuit(variable_qubits=variable_qubits, ancilla_qubits=ancilla_qubits), max_depth=max_depth)
        
best_path = mcts.mcts(root, budget=budget, branches=branches, evaluation_function=problem, criteria=criteria, rollout_type=rollout_type, roll_out_steps=roll_out_steps,
                                choices=choices, epsilon=epsilon, stop_deterministic=stop_deterministic, ucb_value=ucb, pw_C=pw_C, pw_alpha=pw_alpha, verbose=True)

Root Node:
 Tree depth: 0  -  Generated by Action: None  -  Number of Children: 0  -  Visits: 0  -  Value: 0  -  Quantum Circuit (CNOT counts)= 0):
     ┌───┐
v_0: ┤ H ├
     ├───┤
v_1: ┤ H ├
     ├───┤
v_2: ┤ H ├
     ├───┤
v_3: ┤ H ├
     └───┘
Epoch Counter:  0
Node Expanded:
 Tree depth: 1  -  Generated by Action: a  -  Number of Children: 0  -  Visits: 0  -  Value: 0  -  Quantum Circuit (CNOT counts)= 1):
     ┌───┐     
v_0: ┤ H ├─────
     ├───┤     
v_1: ┤ H ├─────
     ├───┤┌───┐
v_2: ┤ H ├┤ X ├
     ├───┤└─┬─┘
v_3: ┤ H ├──■──
     └───┘     
Reward:  -0.09976599014477001
Epoch Counter:  1
Node Expanded:
 Tree depth: 1  -  Generated by Action: a  -  Number of Children: 0  -  Visits: 0  -  Value: 0  -  Quantum Circuit (CNOT counts)= 0):
     ┌───┐              
v_0: ┤ H ├──────────────
     ├───┤              
v_1: ┤ H ├──────────────
     ├───┤┌────────────┐
v_2: ┤ H ├┤ Rx(1.4499) ├
     ├───┤└────────────┘
v_3: ┤ H ├──────────────
     └───┘              
Reward:  0.042078979

Finally it outputs the path that creates the best circuit, starting from the root to the leaf. In the following we print the values of the objective function evaluated on the quantum circuits designed along the best path. Note that, in this formulation, a children node is not necessarily better than the parent.
Remember that this is a minimization problem and the lower the objective value the better the node

In [12]:
quantum_circuit_path = best_path['qc']
cost = []
for i in range(len(quantum_circuit_path)):
    cost.append(problem(quantum_circuit_path[i], cost=True))
    print("Node at depth tree: ", i, "number of children: ", best_path["children"][i])
    print("Objective value: ", cost[i])
    print("Cumulative Reward: ", best_path["value"][i])
    print("Average Reward: ", best_path["value"][i]/best_path["visits"][i], "\n")

Node at depth tree:  0 number of children:  4
Objective value:  -0.04207897977473338
Cumulative Reward:  298.74112765912867
Average Reward:  0.2984426849741545 

Node at depth tree:  1 number of children:  4
Objective value:  -0.04207897977473342
Cumulative Reward:  296.1985787039216
Average Reward:  0.307898730461457 

Node at depth tree:  2 number of children:  4
Objective value:  -0.0745148489402877
Cumulative Reward:  294.39105732541435
Average Reward:  0.31895022462125067 

Node at depth tree:  3 number of children:  4
Objective value:  -0.0745148489402877
Cumulative Reward:  294.17250816333933
Average Reward:  0.3305309080486959 

Node at depth tree:  4 number of children:  4
Objective value:  -0.05357222028567636
Cumulative Reward:  292.828539981584
Average Reward:  0.34169024501935125 

Node at depth tree:  5 number of children:  4
Objective value:  -0.05357222028567636
Cumulative Reward:  290.11200732585536
Average Reward:  0.35379513088518943 

Node at depth tree:  6 number o

At this poit we selct the ansatz as the best quantum circuit found in the path.

In [13]:
ansatz = quantum_circuit_path[cost.index(min(cost))]
print("Selected Ansatz: \n", ansatz)

Selected Ansatz: 
           ┌───┐      ┌────────────┐┌────────────┐
v_0: ─────┤ H ├──────┤ Rz(4.4867) ├┤ Rz(1.4439) ├
          ├───┤     ┌┴────────────┤└────────────┘
v_1: ─────┤ H ├─────┤ Ry(0.77676) ├──────────────
     ┌────┴───┴────┐└─────────────┘              
v_2: ┤ Rx(0.14619) ├─────────────────────────────
     └─┬──────────┬┘┌─────────────┐              
v_3: ──┤ Rz(3.98) ├─┤ Rz(0.83857) ├──────────────
       └──────────┘ └─────────────┘              


## Parameter Optimization
Once we designed the structure of our quantum circuit we optimize the parameters through a classical gradient-based optimizer. Here we chose the ADAM Optimizer

In [14]:
problem(quantum_circuit=ansatz, gradient=True)

Step = 0,  Energy = -0.68118321 Ha
Step = 2,  Energy = -0.68817643 Ha
Step = 4,  Energy = -0.69496031 Ha
Step = 6,  Energy = -0.70152488 Ha
Step = 8,  Energy = -0.70786260 Ha
Step = 10,  Energy = -0.71396928 Ha
Step = 12,  Energy = -0.71984486 Ha
Step = 14,  Energy = -0.72549386 Ha
Step = 16,  Energy = -0.73092513 Ha
Step = 18,  Energy = -0.73615051 Ha
Step = 20,  Energy = -0.74118248 Ha
Step = 22,  Energy = -0.74603146 Ha
Step = 24,  Energy = -0.75070373 Ha
Step = 26,  Energy = -0.75520087 Ha
Step = 28,  Energy = -0.75952059 Ha
Step = 30,  Energy = -0.76365842 Ha
Step = 32,  Energy = -0.76760964 Ha
Step = 34,  Energy = -0.77137086 Ha
Step = 36,  Energy = -0.77494103 Ha
Step = 38,  Energy = -0.77832177 Ha
Step = 40,  Energy = -0.78151711 Ha
Step = 42,  Energy = -0.78453271 Ha
Step = 44,  Energy = -0.78737491 Ha
Step = 46,  Energy = -0.79004984 Ha
Step = 48,  Energy = -0.79256296 Ha
Step = 50,  Energy = -0.79491900 Ha
Step = 52,  Energy = -0.79712224 Ha
Step = 54,  Energy = -0.79917698 

[array(-0.6776117),
 array(-0.68118321),
 array(-0.68470528),
 array(-0.68817643),
 array(-0.69159521),
 array(-0.69496031),
 array(-0.69827055),
 array(-0.70152488),
 array(-0.70472244),
 array(-0.7078626),
 array(-0.71094493),
 array(-0.71396928),
 array(-0.71693579),
 array(-0.71984486),
 array(-0.72269722),
 array(-0.72549386),
 array(-0.72823602),
 array(-0.73092513),
 array(-0.73356276),
 array(-0.73615051),
 array(-0.73868994),
 array(-0.74118248),
 array(-0.74362934),
 array(-0.74603146),
 array(-0.74838947),
 array(-0.75070373),
 array(-0.75297426),
 array(-0.75520087),
 array(-0.75738316),
 array(-0.75952059),
 array(-0.76161255),
 array(-0.76365842),
 array(-0.76565762),
 array(-0.76760964),
 array(-0.76951413),
 array(-0.77137086),
 array(-0.77317979),
 array(-0.77494103),
 array(-0.77665487),
 array(-0.77832177),
 array(-0.77994228),
 array(-0.78151711),
 array(-0.78304698),
 array(-0.78453271),
 array(-0.78597509),
 array(-0.78737491),
 array(-0.78873292),
 array(-0.79004